Mathematical Model of Stock Market Fluctuations



Stock market fluctuations can be modeled using stochastic differential equations (SDEs):


       Geometric Brownian Motion (GBM) – Standard model for stock prices

      Stochastic Volatility – Volatility changes randomly over time

          Jump Diffusion – Sudden price jumps due to news/events



1. Geometric Brownian Motion (GBM)

The simplest model for stock prices is GBM, given by:

         dS(t) = μ S(t) dt + σ S(t) dW(t)

Where:

         S(t): Stock price at time t

          μ: Expected return (drift)

         σ: Constant volatility




W(t): Wiener process (Brownian motion)

Discretized form (Euler-Maruyama scheme):

         S(t+Δt) = S(t) * exp( (μ - σ²/2)Δt + σ√(Δt)ε(t) )

        where ε(t) ~ N(0,1).

2. Stochastic Volatility (Heston Model)

Volatility is not constant—it fluctuates randomly. The Heston model introduces mean-reverting stochastic volatility:


           dS(t) = μ S(t) dt + √v(t) S(t) dW1(t)

           dv(t) = κ(θ - v(t)) dt + ξ √v(t) dW2(t)

Where:

     v(t): Variance (volatility squared, σ(t)²)

      κ: Mean reversion speed

     θ: Long-term average variance

      ξ: Volatility of volatility

     W1(t), W2(t): Correlated Brownian motions with dW1(t)dW2(t) = ρdt

Discretized form:


                   v(t+Δt) = v(t) + κ(θ - v(t))Δt + ξ √v(t) √(Δt) ε2(t)

             Ensuring v(t) > 0 requires special care (e.g., absorbing or reflecting boundary conditions).


3. Jump Diffusion (Merton Model)

Sudden market shocks (e.g., earnings reports, crises) introduce discontinuous jumps:


                    dS(t) = μ S(t) dt + σ S(t) dW(t) + J(t) S(t) dN(t)

Where:

                    N(t): Poisson process (jump arrivals) with intensity λ

                    J(t): Jump size, where ln(1 + J(t)) ~ N(μJ, σJ²)

Discretized form:

           S(t+Δt) = S(t) * exp( (μ - σ²/2)Δt + σ√(Δt)ε(t) ) 
        
          * ∏(1 + Ji) for i = 1 to N(Δt)
          
         where N(Δt) ~ Poisson(λΔt).

4. Combined Model (GBM + Stochastic Volatility + Jumps)

A general stock price model incorporating all effects:


              dS(t) = μ S(t) dt + √v(t) S(t) dW1(t) + J(t) S(t) dN(t)


               dv(t) = κ(θ - v(t)) dt + ξ √v(t) dW2(t)

In [23]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML 


In [24]:
# 1. PARAMETERS

S0 = 100               # Initial price
mu = 0.05              # Drift (5% annual return)
sigma0 = 0.2           # Initial volatility (20%)
T = 1                  # Time horizon (1 year)
dt = 1/252             # Daily steps (252 trading days/year)
n_paths = 5            # Number of Monte Carlo paths  # <-- CRITICAL FIX

# Stochastic volatility (Heston model)
kappa = 3.0            # Mean reversion speed
theta = 0.2**2         # Long-term variance (20% vol)
xi = 0.1               # Volatility of volatility

# Jump parameters (Merton model)
jump_intensity = 0.05  # 5 jumps/year on average
jump_mu = -0.05        # Avg jump size (-5%)
jump_sigma = 0.10      # Jump volatility

In [25]:
# 2. SIMULATION

np.random.seed(42)      # For reproducibility
n_steps = int(T/dt)
t = np.linspace(0, T, n_steps + 1)

# Initialize arrays
S = np.zeros((n_paths, n_steps + 1))
S[:, 0] = S0
v = np.zeros_like(S)
v[:, 0] = sigma0**2     # Start at initial variance

for i in range(n_paths):
    for j in range(1, n_steps + 1):
        # Correlated Brownian motions (ρ = -0.2)
        Z1, Z2 = np.random.normal(0, 1, 2)
        dW1 = np.sqrt(dt) * Z1
        dW2 = np.sqrt(dt) * (-0.2 * Z1 + np.sqrt(1 - 0.2**2) * Z2)
        
        # Heston volatility update (with full truncation fix)
        v_prev = max(v[i, j-1], 0)  # Prevent negative variance
        v[i, j] = v_prev + kappa * (theta - v_prev) * dt + xi * np.sqrt(v_prev) * dW2
        
        # Merton jumps
        jump = 0.0
        if np.random.rand() < jump_intensity * dt:
            jump = np.exp(jump_mu + jump_sigma * np.random.normal()) - 1
        
        # Stock price update
        S[i, j] = S[i, j-1] * np.exp(
            (mu - 0.5 * v_prev) * dt + 
            np.sqrt(v_prev) * dW1 + 
            jump
        )


In [26]:
# 3. ANIMATION

fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(12, 8), height_ratios=[2, 1])
fig.suptitle('Stock Price with Stochastic Volatility & Jumps')

# Initialize lines
price_lines = [ax1.plot([], [], lw=1, label=f'Path {i+1}')[0] for i in range(n_paths)]
vol_lines = [ax2.plot([], [], lw=1, alpha=0.7)[0] for i in range(n_paths)]

# Formatting
ax1.set_xlim(0, T)
ax1.set_ylim(np.min(S)*0.9, np.max(S)*1.1)
ax1.set_ylabel('Price ($)')
ax1.legend(loc='upper left')
ax1.grid(True)

ax2.set_xlim(0, T)
ax2.set_ylim(0, np.max(np.sqrt(v))*1.1)
ax2.set_xlabel('Time (years)')
ax2.set_ylabel('Volatility')
ax2.grid(True)

def animate(frame):
    # Update every 5 frames for smoothness
    frame = min(frame * 5, n_steps)  
    

    for i in range(n_paths):
        price_lines[i].set_data(t[:frame], S[i, :frame])
        vol_lines[i].set_data(t[:frame], np.sqrt(v[i, :frame]))  # Convert variance to vol
    
    return price_lines + vol_lines

# Create animation (reduce frames for performance)
ani = FuncAnimation(
    fig, 
    animate, 
    frames=range(0, n_steps//5 + 1), 
    interval=50, 
    blit=True
)

plt.tight_layout()
plt.close()  # Prevents duplicate display in notebooks

# Display (choose one based on your environment)
HTML(ani.to_jshtml())
